# **Melanoma - Skin Cancer (CNN)**

## **Downloading......**

In [ ]:
! pip install -q kaggle

In [ ]:
! mkdir ~/.kaggle
! cp kaggle.json ~/.kaggle/
! chmod 600 ~/.kaggle/kaggle.json

In [ ]:
! kaggle datasets download -d bhaveshmittal/melanoma-cancer-dataset

 98% 78.0M/79.4M [00:03<00:00, 32.1MB/s]
100% 79.4M/79.4M [00:03<00:00, 24.8MB/s]


In [ ]:
! unzip /content/melanoma-cancer-dataset.zip

Streaming output truncated to the last 5000 lines.
  inflating: train/Malignant/1530.jpg  
  inflating: train/Malignant/1531.jpg  
  inflating: train/Malignant/1532.jpg  
  inflating: train/Malignant/1533.jpg  
  inflating: train/Malignant/1534.jpg  
  inflating: train/Malignant/1535.jpg  
  inflating: train/Malignant/1536.jpg  
  inflating: train/Malignant/1537.jpg  
  inflating: train/Malignant/1538.jpg  
  inflating: train/Malignant/1539.jpg  
  inflating: train/Malignant/154.jpg  
  inflating: train/Malignant/1540.jpg  
  inflating: train/Malignant/1541.jpg  
  inflating: train/Malignant/1542.jpg  
  inflating: train/Malignant/1543.jpg  
  inflating: train/Malignant/1544.jpg  
  inflating: train/Malignant/1545.jpg  
  inflating: train/Malignant/1546.jpg  
  inflating: train/Malignant/1547.jpg  
  inflating: train/Malignant/1548.jpg  
  inflating: train/Malignant/1549.jpg  
  inflating: train/Malignant/155.jpg  
  inflating: train/Malignant/1550.jpg  
  inflating: train/Malignant/15

## **Processing.....**

In [ ]:
import numpy as np

from torchvision.datasets import ImageFolder
from torchvision import transforms
from torch.utils.data import DataLoader

In [ ]:
transform = transforms.Compose(
    [
        transforms.ToTensor(),
        transforms.Resize(size = (224, 224)),
        transforms.RandomRotation(degrees = (-10, 10)),
        transforms.Normalize(mean = (0.5, 0.5, 0.5), std = (0.5, 0.5, 0.5))
    ]
)

In [ ]:
train_folder = ImageFolder(
    root = "/content/train",
    transform = transform
)

test_folder = ImageFolder(
    root = "/content/test",
    transform = transform
)

In [ ]:
train_folder

Dataset ImageFolder
    Number of datapoints: 11879
    Root location: /content/train
    StandardTransform
Transform: Compose(
               ToTensor()
               Resize(size=(224, 224), interpolation=bilinear, max_size=None, antialias=warn)
               RandomRotation(degrees=[-10.0, 10.0], interpolation=nearest, expand=False, fill=0)
               Normalize(mean=(0.5, 0.5, 0.5), std=(0.5, 0.5, 0.5))
           )

In [ ]:
test_folder

Dataset ImageFolder
    Number of datapoints: 2000
    Root location: /content/test
    StandardTransform
Transform: Compose(
               ToTensor()
               Resize(size=(224, 224), interpolation=bilinear, max_size=None, antialias=warn)
               RandomRotation(degrees=[-10.0, 10.0], interpolation=nearest, expand=False, fill=0)
               Normalize(mean=(0.5, 0.5, 0.5), std=(0.5, 0.5, 0.5))
           )

In [ ]:
train_loader = DataLoader(
    dataset = train_folder,
    batch_size = 25,
    shuffle = True
)

test_loader = DataLoader(
    dataset = test_folder,
    batch_size = 25,
    shuffle = True
)

## **Intialising.....**

In [ ]:
import torch
import torch.nn as nn
from torch import FloatTensor, LongTensor, manual_seed

In [ ]:
class CNN(nn.Module):

  def __init__(self):
    super().__init__()

    self.conv1 = nn.Conv2d(
        in_channels = 3,
        out_channels = 6,
        kernel_size = (3, 3),
        padding = (1, 1),
        stride = 1
    )

    self.conv2 = nn.Conv2d(
        in_channels = 6,
        out_channels = 9,
        kernel_size = (5, 5),
        padding = (0, 0),
        stride = 1
    )

    self.max_pool = nn.MaxPool2d(
        kernel_size = (2, 2),
        stride = 1,
        padding = 0
    )

    self.flatten = nn.Flatten()

    self.fc_layers = nn.Sequential(
        nn.Linear(in_features = 427716, out_features = 128),
        nn.ReLU(),
        nn.Linear(in_features = 128, out_features = 84),
        nn.ReLU(),
        nn.Linear(in_features = 84, out_features = 2)
    )

  def forward(self, x):
    x = self.conv1(x)
    x = self.max_pool(x)
    x = self.conv2(x)
    x = self.max_pool(x)

    x = self.flatten(x)

    x = self.fc_layers(x)
    return x

In [ ]:
device : str = "cuda" if torch.cuda.is_available() else "cpu"
device

'cuda'

In [ ]:
manual_seed(42)

In [ ]:
Model = CNN().to(device)

In [ ]:
Model

CNN(
  (conv1): Conv2d(3, 6, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
  (conv2): Conv2d(6, 9, kernel_size=(5, 5), stride=(1, 1))
  (max_pool): MaxPool2d(kernel_size=(2, 2), stride=1, padding=0, dilation=1, ceil_mode=False)
  (flatten): Flatten(start_dim=1, end_dim=-1)
  (fc_layers): Sequential(
    (0): Linear(in_features=427716, out_features=128, bias=True)
    (1): ReLU()
    (2): Linear(in_features=128, out_features=84, bias=True)
    (3): ReLU()
    (4): Linear(in_features=84, out_features=2, bias=True)
  )
)

## **Training.....**

In [ ]:
loss_fn = nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(Model.parameters(), lr = 0.001)

In [ ]:
epochs = 5

training_losses = []
testing_losses = []
training_accuracies = []
testing_accuracies = []

for epoch in range(epochs):

  Model.train()

  training_correct = 0
  for batch, (x_train, y_train) in enumerate(train_loader):
    x_train, y_train = x_train.to(device), y_train.to(device)

    y_pred = Model(x_train)
    loss = loss_fn(y_pred, y_train)

    training_correct += (torch.max(y_pred, 1)[1] == y_train).sum()
    training_losses.append(loss.item())

    optimizer.zero_grad()
    loss.backward()
    optimizer.step()

    if (batch + 1) % 100 == 0:
      print(f"Epoch : {epoch + 1} | Batch : {batch + 1} | Loss : {loss.item()}")
  training_accuracies.append(training_correct / len(train_loader.dataset))

  Model.eval()

  with torch.no_grad():
    testing_correct = 0
    for batch, (x_test, y_test) in enumerate(test_loader):
      x_test, y_test = x_test.to(device), y_test.to(device)

      y_pred = Model(x_test)
      loss = loss_fn(y_pred, y_test)

      testing_losses.append(loss.item())
      testing_correct += (torch.argmax(y_pred, 1) == y_test).sum()
      if (batch + 1) % 100 == 0:
        print(f"Epoch : {epoch + 1} | Validation Batch : {batch + 1} | Validation Loss : {loss.item()}")
    testing_accuracies.append(testing_correct / len(test_loader.dataset))

  print(f"Epoch : {epoch + 1} | Training Acc : {training_accuracies[-1]} | Validation Acc : {testing_accuracies[-1]}")

Epoch : 1 | Batch : 100 | Loss : 0.3202607333660126
Epoch : 1 | Batch : 200 | Loss : 0.32595473527908325
Epoch : 1 | Batch : 300 | Loss : 0.39812010526657104
Epoch : 1 | Batch : 400 | Loss : 0.20087194442749023
Epoch : 1 | Training Acc : 0.8419058322906494 | Validation Acc : 0.8795000314712524
Epoch : 2 | Batch : 100 | Loss : 0.2786577641963959
Epoch : 2 | Batch : 200 | Loss : 0.23820114135742188
Epoch : 2 | Batch : 300 | Loss : 0.2942928969860077
Epoch : 2 | Batch : 400 | Loss : 0.28820371627807617
Epoch : 2 | Training Acc : 0.8570586442947388 | Validation Acc : 0.8860000371932983
Epoch : 3 | Batch : 100 | Loss : 0.2471906840801239
Epoch : 3 | Batch : 200 | Loss : 0.2775031328201294
Epoch : 3 | Batch : 300 | Loss : 0.32207241654396057
Epoch : 3 | Batch : 400 | Loss : 0.1883620023727417
Epoch : 3 | Training Acc : 0.8648875951766968 | Validation Acc : 0.862500011920929
Epoch : 4 | Batch : 100 | Loss : 0.33406805992126465
Epoch : 4 | Batch : 200 | Loss : 0.3141508400440216
Epoch : 4 | Ba

## **Testing.....**

In [ ]:
Model.eval()

correct = 0
y_testing = []
y_predicted = []

with torch.no_grad():
  for _, (x_test, y_test) in enumerate(test_loader):
    x_test, y_test = x_test.to(device), y_test.to(device)
    y_pred = torch.argmax(Model(x_test), 1)
    correct += (y_pred == y_test).sum()

    for i, j in zip(y_pred, y_test):
      y_predicted.append(i.cpu())
      y_testing.append(j.cpu())

print(f"Accuracy : {correct / len(test_loader.dataset) * 100} %")

Accuracy : 86.35000610351562 %


In [ ]:
from sklearn.metrics import classification_report
print(classification_report(y_pred = y_predicted, y_true = y_testing))

              precision    recall  f1-score   support

           0       0.85      0.88      0.87      1000
           1       0.88      0.84      0.86      1000

    accuracy                           0.86      2000
   macro avg       0.86      0.86      0.86      2000
weighted avg       0.86      0.86      0.86      2000



In [ ]:
test_folder.class_to_idx

{'Benign': 0, 'Malignant': 1}

In [ ]:
classes = {
    0 : "Benign",
    1 : "Malignant"
}

In [ ]:
import matplotlib.pyplot as plt
%matplotlib inline

In [92]:
from random import randint

Model.eval()
fig = plt.figure(figsize = (80, 200))

for i in range(50):
  j = i
  i = randint(0, 2000)
  fig.add_subplot(10, 5, j + 1)
  plt.imshow(test_loader.dataset[i][0].detach().numpy().transpose(2, 1, 0))

  with torch.no_grad():
    pred = Model(test_loader.dataset[i][0].view(1, 3, 224, 224).to(device))
    pred = torch.argmax(pred, 1)[0]

  plt.title(f"True Label : {classes[test_loader.dataset[i][1]]} \nPredicted Label : {classes[pred.item()]}", fontdict = {"fontsize" : 50})

## **Saving.....**

In [93]:
torch.save(Model.state_dict(), "SkinCancer_CNN.pt")